# Extração e seleção de características

As características que são extraídas dos dados dependem de sua natureza. Os dados EMG são sinais elétricos coletados dentro de um período de tempo, portanto são dados no domínio do tempo. As características deste domínio são extraídas dele. Também é possível transformar os dados EMG para o domínio da frequência e extrair características neste domínio. Existem diversas características que podem ser extraídas de cada domínio, entretando nem todas elas serão relevantes. Cada problema se beneficia de características ou combinações delas. Portanto, é preciso que haja uma seleção de características para encontrar a combinação de características que trará melhor resultado na posterior classificação dos dados.

## Reutilizando os passos anteriores

É necessário carregar os dados pré-processados, para dar início à extração de características. No jupyter notebook podemos utilizar o namespace completo de outro notebook:

In [2]:
%run preprocessing.ipynb

(20000, 2)
(10, 6, 20000, 2) - (classes, ensaios, linhas, canais)
(10, 6, 2, 20000) - (classes, ensaios, canais, linhas)
(10, 6, 2, 20000) - (classes, ensaios, canais, linhas)
(10, 6, 2, 20000) - (classes, ensaios, canais, linhas)
(10, 6, 2, 20000) - (classes, ensaios, canais, linhas)
(10, 6, 2, 20000) - (classes, ensaios, canais, linhas)
(10, 6, 2, 20000) - (classes, ensaios, canais, linhas)
(10, 6, 2, 20000) - (classes, ensaios, canais, linhas)
(10, 6, 2, 20000) - (classes, ensaios, canais, linhas)
(10, 6, 2, 20000) - (classes, ensaios, canais, linhas)
(10, 6, 2, 20000) - (classes, ensaios, canais, linhas)
(10, 6, 2, 20000) - (classes, ensaios, canais, linhas)
 (60, 2, 20000)
Formato (shape) dos dados depois da divisão de janelas
Dominio do tempo: (60, 2, 41, 1024) - (classes+ensaios, canais, janelas, linhas)
Dominio da frequência:  (60, 2, 41, 513) - (classes+ensaios, canais, janelas, linhas)


Uma característica é uma propriedade individual mensurável ou característica de um fenômeno que está sendo observado. Em EMG, uma característica pode ser extraída no domínio do tempo ou no domínio da frequência. As características a seguir foram retiradas do artigo *EMG Feature Extraction for Tolerance of White Gaussian Noise* \[1\].

### Domínio do tempo

1. Willison Amplitude (WAMP)

    > $ \sum_{i=1}^{N-1}f(|x_i - x_{i+1}|) \\$
    $ sgn(x) = \begin{cases} 1 & \text{if } x \geq threshold \\ 0 & \text{otherwise} \end{cases} $

2. Variance of EMG (VAR-E)

    > $ \frac{1}{N}\sum_{i=1}^{N}x_i^2 $

3. Root Mean Square (RMS)

    > $ \sqrt{\frac{1}{N-1}\sum_{i=1}^{N}|x_i|^2} $

4. Waveform Length (WL)
    
    > $ \sum_{i=1}^{N-1}|x_{i+1} - x_i| $

5. Zero Crossing (ZC)

    > $ \sum_{i=1}^{N}[sgn(x_i x_{i+1}) \cap |x_i - x_{i+1}| \geq threshold] \\$
    $ sgn(x) = \begin{cases} 1 & \text{if } x \geq threshold \\ 0 & \text{otherwise} \end{cases} $

### Domínio da frequência

1. Auto Regressive (AR)

    > $ - \sum_{j=1}^{\rho}\alpha_j x_{j-1} + w_n $

2. Median Frequency (FMD)

    > $ \frac{1}{2}\sum_{j=1}^{M}PSD_j $

3. Mean Frequency (FMN)

    > $ \sum_{j=1}^{M}f_j PSD_j \Big{ / } \sum_{j=1}^{M}PSD_j $

4. Modified Median Frequency (MMDF)

    > $ \frac{1}{2}\sum_{i=1}^{M}A_j $


\[1\] Phinyomark, Angkoon & Limsakul, Chusak & Phukpattaranont, P.. (2008). EMG Feature Extraction for Tolerance of White Gaussian Noise.
[Disponível neste link](https://www.researchgate.net/publication/263765853_EMG_Feature_Extraction_for_Tolerance_of_White_Gaussian_Noise)

**Desafio 1**: Descrever as características de acordo com o artigo citado e outros disponíveis relacionados. O que está querendo "ser visto" em cada característica? Qual é o significado matemático de cada uma delas?

### Extraindo características

É necessário implementar as características, geralmente em formato de funções ou métodos, para que seja possível aplicar tais funções aos dados de entrada e obter as características resultantes. A seguir temos a implementação das características VAR & RMS (domínio do tempo) e FDM & MMDF (domínio da frequência).

In [44]:
from math import prod

# funções auxiliares
def PSD(w):
    ''' definição da função PSD para o sinal no domínio da frequência '''
    return np.abs(w) ** 2


# funções de extração de características

def wamp(x, th):
    res = np.abs(np.diff(x))
    return np.sum(res >= th, axis=-1)

def var(x):
    return np.sum(x ** 2, axis=-1) / (np.prod(x.shape[:-1]) - 1)

def rms(x):
    return np.sqrt(np.sum(np.abs(x) ** 2, axis=-1) / (np.prod(x.shape[:-1]) - 1))

def fmd(w):
    return np.sum(PSD(w), axis=-1) / 2

def mmdf(w):
    return np.sum(np.abs(w), axis=-1) / 2

In [72]:
def moda(x):
    vals,counts = np.unique(x, return_counts=True)
    mode_value = np.argwhere(counts == np.max(counts))
    print(vals)
    
    return mode_value.flatten().tolist(), vals, counts

In [73]:
from scipy import stats

th = np.median(chunks_time)
avr = np.mean(chunks_time)
m, vals, counts = moda(chunks_time)

[-0.00378144 -0.00368428 -0.00359885 ...  0.00188989  0.00193046
  0.00196623]


In [81]:
np.median(vals)

2.4366987985769027e-06

In [75]:

for k in m:
    print(vals[k], counts[k])

-0.003781439771678742 3
-0.0035763166142758094 3
-0.003532973279770977 3
-0.002952508640525605 3
-0.002839383343453261 3
-0.002733032817035395 3
-0.002592603417901671 3
-0.002523967844208021 3
-0.0024348007903216493 3
-0.0024002556674068993 3
-0.002114067943067541 3
-0.002048119158959756 3
-0.0020354350024573576 3
-0.0020211646474989535 3
-0.0019680044030814564 3
-0.001881763592215186 3
-0.0018402884322805996 3
-0.0018258717666937289 3
-0.0018216105273226562 3
-0.0018207398095707254 3
-0.0018202206817494767 3
-0.0017859270384066534 3
-0.0017819826779412518 3
-0.0017624568411553146 3
-0.0017483528152443465 3
-0.0017399463904892193 3
-0.0017356382116825368 3
-0.0017081066449367295 3
-0.0016774040213595313 3
-0.0016764961191327082 3
-0.0016758348047359152 3
-0.0016541789165687038 3
-0.0016474751754683265 3
-0.0016164230063025699 3
-0.0016057973199410348 3
-0.0016047256575857038 3
-0.0016021311598199296 3
-0.0016005657914825234 3
-0.001584613987721001 3
-0.001577830557643845 3
-0.001566027

-0.0003263024147138828 3
-0.0003262910880790422 3
-0.00032628899489751153 3
-0.00032628700362279 3
-0.0003262852371424086 3
-0.00032628495869146317 3
-0.00032628432714384623 3
-0.0003262676711930308 3
-0.00032626326737895234 3
-0.0003262549843063049 3
-0.00032623628070639805 3
-0.00032620806789650936 3
-0.0003262007212179737 3
-0.0003261718473730774 3
-0.0003261674479497443 3
-0.00032615560881246774 3
-0.00032614279593223887 3
-0.0003261303947497117 3
-0.00032612725019821 3
-0.0003261214448685885 3
-0.00032611802646923443 3
-0.00032610716342524693 3
-0.00032610402559352596 3
-0.00032609206206100504 3
-0.0003260845803455064 3
-0.00032608346543614727 3
-0.00032607634605595517 3
-0.0003260744075484045 3
-0.0003260553766182557 3
-0.00032604841324040767 3
-0.0003260465002465668 3
-0.0003260388382693198 3
-0.00032603145778071563 3
-0.0003260313135388422 3
-0.00032602758113066074 3
-0.00032601840506081743 3
-0.0003260040324483224 3
-0.0003260031931873838 3
-0.0003260017739696023 3
-0.00032600

-0.00022894179138142242 3
-0.00022893977514504922 3
-0.00022893116451276223 3
-0.00022892353810677733 3
-0.0002289221578250951 3
-0.00022892178511988676 3
-0.0002289164864188431 3
-0.00022891194027380756 3
-0.00022890894459701063 3
-0.00022890755199962766 3
-0.00022890632052114692 3
-0.00022890556880234876 3
-0.0002288975158214744 3
-0.0002288973825214373 3
-0.0002288960023947857 3
-0.00022889021815861618 3
-0.0002288855413829755 3
-0.0002288854321005694 3
-0.00022888214255491245 3
-0.00022888129641449333 3
-0.00022887065290747282 3
-0.00022885351800094493 3
-0.000228851014029046 3
-0.00022884513797811722 3
-0.00022883718679371048 3
-0.00022883325474816387 3
-0.00022883023932925256 3
-0.00022882956995399053 3
-0.00022882840368505352 3
-0.0002288232283215746 3
-0.00022882122784177006 3
-0.00022881904627995592 3
-0.00022880443114070347 3
-0.00022879820520482194 3
-0.00022879573693131963 3
-0.0002287892409916295 3
-0.00022878812682320987 3
-0.0002287875419216414 3
-0.00022878172555409326 

-0.00017551054000537189 3
-0.00017550955614201988 3
-0.00017550709658338152 3
-0.00017550609685904457 3
-0.00017550365638631098 3
-0.0001754994692449429 3
-0.00017549873154684698 3
-0.0001754977296358247 3
-0.0001754959854955071 3
-0.00017548975846906425 3
-0.00017548939019264797 3
-0.00017548903384164468 3
-0.00017547934590693838 3
-0.0001754790461411934 3
-0.0001754780288106711 3
-0.00017547716252582917 3
-0.00017547603383160674 3
-0.00017547592629308178 3
-0.00017547580289528817 3
-0.00017546533157434467 3
-0.0001754650112583147 3
-0.00017545792998733794 3
-0.00017545154990541737 3
-0.00017545050886745312 3
-0.00017544931777471742 3
-0.00017543960284459347 3
-0.00017543292137495438 3
-0.00017542959308853616 3
-0.0001754249475902289 3
-0.00017542432170645884 3
-0.00017542328820121354 3
-0.00017542321046125687 3
-0.0001754197514313636 3
-0.00017541622484097347 3
-0.0001754142446379069 3
-0.00017541351857470268 3
-0.0001754081422836074 3
-0.00017540763704269332 3
-0.0001754070552464732

-0.00013761549454144353 3
-0.0001376135326494847 3
-0.0001376112940204726 3
-0.00013761114153435 3
-0.00013760791826496592 3
-0.00013760561550690711 3
-0.00013760560844949316 3
-0.00013760204262229422 3
-0.00013759996961139307 3
-0.00013759421200149546 3
-0.00013759017918240493 3
-0.00013758966892281962 3
-0.00013758929126012648 3
-0.0001375886129490068 3
-0.0001375866057602193 3
-0.00013758488027254748 3
-0.00013758483082390013 3
-0.00013758423902992208 3
-0.00013758008162538282 3
-0.0001375782574238727 3
-0.00013757793565355176 3
-0.00013757022457319226 3
-0.00013756782157087034 3
-0.00013756759333301584 3
-0.00013756725734708283 3
-0.00013756466590280603 3
-0.00013756439204353168 3
-0.00013756193709419583 3
-0.00013755777771537976 3
-0.00013755603862657646 3
-0.00013755526225706663 3
-0.00013755217866888095 3
-0.00013755171920238067 3
-0.00013754943621150314 3
-0.00013754742639713452 3
-0.00013754700297690162 3
-0.0001375465547161824 3
-0.00013754525384725264 3
-0.000137539614148289

...

3.8668897480381356e-05 3
3.866905559803898e-05 3
3.867011991055521e-05 3
3.86703833505102e-05 3
3.86706650624035e-05 3
3.867145032409517e-05 3
3.867149489314434e-05 3
3.867196536014255e-05 3
3.86721726123042e-05 3
3.8673177652081983e-05 3
3.867345765822707e-05 3
3.8673925800566865e-05 3
3.86747174756741e-05 3
3.867639774426838e-05 3
3.867656504724287e-05 3
3.8676798485095e-05 3
3.867815647044927e-05 3
3.8681801897684354e-05 3
3.868296963213297e-05 3
3.868441249631773e-05 3
3.8684618791301196e-05 3
3.868501303266781e-05 3
3.868572451079027e-05 3
3.8686303068448506e-05 3
3.8686415262762065e-05 3
3.8686616902186746e-05 3
3.868675808031213e-05 3
3.868699413562238e-05 3
3.8687795491843605e-05 3
3.8688498176709e-05 3
3.868859525863784e-05 3
3.868885266200325e-05 3
3.8690057262471177e-05 3
3.869035468080904e-05 3
3.869060298383528e-05 3
3.869061033229674e-05 3
3.8691542912489724e-05 3
3.8692679677846e-05 3
3.8693719533354194e-05 3
3.86942075296242e-05 3
3.869499837819715e-05 3
3.8695146123154

4.9206771679630734e-05 3
4.920696365424863e-05 3
4.920714185287528e-05 3
4.92076872307484e-05 3
4.9208704416594554e-05 3
4.920883865759314e-05 3
4.920950040432949e-05 3
4.920994877602378e-05 3
4.921122342356885e-05 3
4.921169236711337e-05 3
4.921182142233762e-05 3
4.921278582915222e-05 3
4.92150680618829e-05 3
4.921785031475836e-05 3
4.92181103639189e-05 3
4.9218471842102935e-05 3
4.9218748130407304e-05 3
4.921947962182636e-05 3
4.9220290753596634e-05 3
4.922056327661842e-05 3
4.922072620703246e-05 3
4.92210202495946e-05 3
4.922202937019702e-05 3
4.9222496984967446e-05 3
4.9222820061329956e-05 3
4.9225221551837156e-05 3
4.922536747592341e-05 3
4.922782693724336e-05 3
4.9228836788027294e-05 3
4.92298384422374e-05 3
4.92299658124376e-05 3
4.923023585367477e-05 3
4.9230299637496145e-05 3
4.923182703727141e-05 3
4.923206805126479e-05 3
4.923208853730791e-05 3
4.923212232872862e-05 3
4.923313196171484e-05 3
4.9233329994967354e-05 3
4.9234773089518986e-05 3
4.923646370052395e-05 3
4.92373320

6.112570850780194e-05 3
6.112686316423358e-05 3
6.11275487478857e-05 3
6.112770444279797e-05 3
6.112786406314899e-05 3
6.112859467284771e-05 3
6.113010684858574e-05 3
6.113051904190538e-05 3
6.113090990271006e-05 3
6.113136919715516e-05 3
6.113227672929208e-05 3
6.113245301814846e-05 3
6.113397047108308e-05 3
6.113541745889324e-05 3
6.113661376689028e-05 3
6.113808674260736e-05 3
6.113857842323548e-05 3
6.114098236096211e-05 3
6.114104395567977e-05 3
6.114152659179407e-05 3
6.114353455484808e-05 3
6.114690369786876e-05 3
6.114792764973887e-05 3
6.114887597186173e-05 3
6.114961030248302e-05 3
6.115190068643276e-05 3
6.115361655050502e-05 3
6.115721290862859e-05 3
6.115988445220192e-05 3
6.116198147751708e-05 3
6.116231189605328e-05 3
6.116236759768758e-05 3
6.116282443615035e-05 3
6.116351912028274e-05 3
6.116373820217281e-05 3
6.116693321965134e-05 3
6.116697047953879e-05 3
6.116926057875276e-05 3
6.116938350103548e-05 3
6.116974132545642e-05 3
6.11717669537191e-05 3
6.117300363288449e

7.60218788177184e-05 3
7.60237056728445e-05 3
7.602377555116122e-05 3
7.602388663853954e-05 3
7.602444637714947e-05 3
7.602583053891697e-05 3
7.602795601485609e-05 3
7.602892673192662e-05 3
7.603021069685179e-05 3
7.603245801806726e-05 3
7.603255421332113e-05 3
7.603457464504614e-05 3
7.603553798991679e-05 3
7.603608021194694e-05 3
7.603627794609405e-05 3
7.603628873045087e-05 3
7.60367454952005e-05 3
7.603681671348176e-05 3
7.603683772738391e-05 3
7.603776358314905e-05 3
7.603842521845504e-05 3
7.603948984686856e-05 3
7.604073267312582e-05 3
7.604123115101811e-05 3
7.604149558189254e-05 3
7.604275330793116e-05 3
7.604373458257331e-05 3
7.604468275589646e-05 3
7.604525950863922e-05 3
7.60457431617666e-05 3
7.604766262696703e-05 3
7.604854342017727e-05 3
7.605295890661375e-05 3
7.605344587645585e-05 3
7.605374490307641e-05 3
7.605470226945763e-05 3
7.605546007784132e-05 3
7.605626759309711e-05 3
7.605733900146523e-05 3
7.605873898430278e-05 3
7.605980469239964e-05 3
7.606239388753753e-0

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [85]:
wamp(chunks_time, th)

array([[[ 965,  957,  967, ...,  986,  988,  983],
        [ 878,  898,  914, ...,  934,  942,  932]],

       [[ 984,  989,  980, ...,  970,  982,  986],
        [ 923,  945,  958, ...,  927,  920,  915]],

       [[ 939,  960,  963, ...,  984,  986,  985],
        [ 840,  878,  904, ...,  950,  929,  927]],

       ...,

       [[ 994,  988,  989, ...,  990,  992, 1003],
        [ 972,  977,  975, ...,  970,  968,  956]],

       [[ 963,  965,  982, ...,  992,  990,  987],
        [ 947,  951,  966, ...,  945,  955,  955]],

       [[ 945,  974,  985, ...,  991,  994,  999],
        [ 915,  941,  956, ...,  943,  980,  982]]])

array([[[ 965,  957,  967, ...,  986,  988,  983],
        [ 878,  898,  914, ...,  934,  942,  932]],

       [[ 984,  989,  980, ...,  970,  982,  986],
        [ 923,  945,  958, ...,  927,  920,  915]],

       [[ 939,  960,  963, ...,  984,  986,  985],
        [ 840,  878,  904, ...,  950,  929,  927]],

       ...,

       [[ 994,  988,  989, ...,  990,  992, 1003],
        [ 972,  977,  975, ...,  970,  968,  956]],

       [[ 963,  965,  982, ...,  992,  990,  987],
        [ 947,  951,  966, ...,  945,  955,  955]],

       [[ 945,  974,  985, ...,  991,  994,  999],
        [ 915,  941,  956, ...,  943,  980,  982]]])

In [9]:
mmdf(chunks_freq).shape

(60, 2, 41)

In [27]:
chunks_time[0][0][0][0:2]
np.abs(chunks_time[0][0][0][0] - chunks_time[0][0][0][1])

5.29034022966353e-05

In [82]:
chunks_time.shape

(60, 2, 41, 1024)

In [91]:
chunks_time.shape

(60, 2, 41, 1024)

In [141]:
getWAMP(chunks_time[0][0][0], 0.0001)

70

In [142]:
# wamp(chunks_time, 0.0001)[0][0][0].shape
mmdf(chunks_freq).shape

(60, 2, 41)

In [132]:
wamp(chunks_time, 0.0001).shape

(60, 41, 1023)

In [139]:
tmp = []
for i in range(60):
    for y in range(2):
        for o in range(41):
            tmp.append(getWAMP(chunks_time[i][y][o], 0.0001))
tmp_final = np.array(tmp)
tmp_final.shape

(4920,)

**Desafio 2**: Implemente todas as características apresentadas neste tutorial em formato de funções. Sinta-se livre também para buscar e implementar características EMG além das apresentadas, citando as fontes de tais características.


## Vetor de características

Ao final da implementação e seleção das características, deve ser escolhida as características e então teremos um vetor com todas elas implementadas.

O vetor de características estará organizado da seguinte forma (exemplo p/ VAR, RMS, RDM e MMDF):

| ID sample | VAR1 | RMS1 | FMD1 | MMDF1 | VAR2 | RMS2 | FMD2 | MMDF2 | Classe |
|:---------:|:----:|:----:|:----:|:-----:|------|------|------|-------|:------:|
|     1     |  v1  |  v1  |  v1  |   v1  | v1   | v1   | v1   | v1    |    0   |
|     2     |  v2  |  v2  |  v2  |   v2  | v2   | v2   | v2   | v2    |    0   |
|    ...    |  ... |  ... |  ... |  ...  | ...  | ...  | ...  | ...   |   ...  |
|     N     |  vN  |  vN  |  vN  |   vN  | vN   | vN   | vN   | vN    |    7   |

## Implementação do vetor

In [3]:
final_data = list()
final_data.append(var(chunks_time))
final_data.append(rms(chunks_time))
final_data.append(fmd(chunks_freq))
final_data.append(mmdf(chunks_freq))

final = np.array(final_data)
final.shape

(4, 60, 2, 41)

É necessário que seja reordenado as dimensões do vetor de características, pois cada característica (de cada canal), deve corresponder à última dimensão do vetor. Por fim, as outras dimensões são concatenadas para o número de amostras.

In [4]:
data = final.transpose(1, 3, 2, 0)
X = data.reshape(data.shape[0]*data.shape[1], data.shape[2]*data.shape[3])
X.shape

(2460, 8)

## Seleção de características

Nesta etapa, são selecionadas as características que mais afetam positivamente no resultado final da classificação. Vamos estudar os métodos de seleção de características nesta [página do projeto sklearn](https://scikit-learn.org/stable/modules/feature_selection.html).

**Desafio 3**: mostrar o resultado para os dados de trabalho, para os seguintes métodos seleção de características:
- VarianceThreshold
- Univariate feature selection
    - escolha o que mais for "interessante": `SelectKBest`, `SelectPercentile` e `GenericUnivariateSelect`
- Recursive feature elimination
- Sequential Feature Selection